## <font color =#FF0000>Wikipedia爬蟲練習</font>
### 範例：練習是從Wikipedia中爬取文章。先定義一個搜尋的關鍵字，擷取該關鍵字詞的文章。

In [17]:
import requests
from bs4 import BeautifulSoup
from fake_useragent import UserAgent
import re
import os
import time
from retrying import retry

def mkdirr(path):
    folder = os.path.exists(path)
    if(folder == True):
        print(path+' 目錄已存在')
    else:
        os.mkdir(path)
        print('建立成功')
        
path = 'd:\\tommy\\WikiArticle'
mkdirr(path)

d:\tommy\WikiArticle 目錄已存在


### <font color =#FF0000> 先定義一個我們想搜尋的字詞，並將它轉換成UTF-8編碼後的URL</font>

In [12]:
key_word = ' 新世紀福音戰士'

utf8_url = repr(key_word.encode('UTF-8')).upper()  # 編碼成UTF-8並轉成大寫字元
utf8_url = utf8_url.replace("\\X", "%")                 # 用 '%' 取代 '\X' 

print("%s: %s" % (key_word, utf8_url[2:-1:1]))     # 擷取中間的編碼結果

# 組成Wiki關鍵字搜尋的網址格式
root_keyword_link = '/wiki/' + utf8_url[2:-1:1]
print(root_keyword_link)



 新世紀福音戰士:  %E6%96%B0%E4%B8%96%E7%B4%80%E7%A6%8F%E9%9F%B3%E6%88%B0%E5%A3%AB
/wiki/ %E6%96%B0%E4%B8%96%E7%B4%80%E7%A6%8F%E9%9F%B3%E6%88%B0%E5%A3%AB


## <font color=#FF0000>範例1：送出關鍵字請求後，爬取該關鍵字的文章內容</font>


In [13]:
ua = UserAgent()
header = {'user-agent': ua.random}

url = 'https://zh.wikipedia.org' + root_keyword_link
res = requests.get(url, headers=header)
soup = BeautifulSoup(res.text, "lxml")

#換語言
lang = soup.find('ul',attrs={'class':"menu vector-menu-content-list"}).find_all('li')
for j in lang:
    if(j.a['lang']=='zh-Hant-TW'):
        print(j.a['href'])
        lang_type = j.a['href']
        
        
url_new = 'https://zh.wikipedia.org' + lang_type
print(url_new)
res_new = requests.get(url_new, headers=header)
soup_new = BeautifulSoup(res_new.text, "lxml")
result_new = soup_new.find('div',attrs={'id':"mw-content-text"}).find('div',attrs={'class':"mw-parser-output"}).find_all('p')
for i in result_new:
    print(i.text)
    


/zh-tw/%E6%96%B0%E4%B8%96%E7%BA%AA%E7%A6%8F%E9%9F%B3%E6%88%98%E5%A3%AB
https://zh.wikipedia.org/zh-tw/%E6%96%B0%E4%B8%96%E7%BA%AA%E7%A6%8F%E9%9F%B3%E6%88%98%E5%A3%AB
《新世紀福音戰士》（日語：新世紀エヴァンゲリオン[注釋 1]；英語：Neon Genesis Evangelion[注釋 2]，通常被稱為EVANGELION[11]、NGE[12][13][14][15]或者EVA[5][16][17][18]。在華語圈中被翻譯為新世紀福音戰士[注釋 3][5][20]，中國大陸早期引進時譯為新世紀天鷹戰士[21][22]）是一部由庵野秀明執導，GAINAX和龍之子製作公司製作的日本動畫電視連續劇，於1995年10月至1996年3月在東京電視台首播。原版的日語配音演員，包括為碇真嗣配音的配音演員及歌手緒方惠美，為綾波零配音的林原惠和為惣流·明日香·蘭格雷配音的宮村優子等。劇中音樂由鷺巢詩郎製作，配樂專輯一經推出就登頂公信榜排行榜；動畫主題曲在其發布後的十幾年間有著持續的影響力。其他新世紀福音戰士系列作品還包括分別於1997年和1998年上映的三部電影，以及被稱作新劇場版的電影四部曲系列作，另外還有其他一些衍生動畫、漫畫和電子遊戲系列。

《新世紀福音戰士》[注釋 4]是一部有著機甲風格的後世界末日動畫。故事背景設置在未來、一場世界性的大災難發生十五年後的東京。故事圍繞著主人公——一名十幾歲的男孩碇真嗣，突然被神秘組織NERV招募去駕駛一種巨大的的生物兵器——EVA，與被稱為使徒的可怕不明敵人進行戰鬥而展開。故事最初著重表現戰鬥場景和人物之間的對話，隨著故事情節的發展，逐漸轉為對人物內心世界的剖析。

《EVA》整個系列突出呈現宗教象徵和主題（英語：Religious symbol），包括卡巴拉、基督教、猶太教以及神道教意象，被譽為20世紀90年代最成功和最負盛名的日本動畫之一。動畫業界和許多動漫欣賞者也將其視為日本最偉大的動畫之一。《EVA》同樣也是最受爭議的動畫電視連續劇之一。其同時混搭批判和機甲風格的解構，使得系列成為一種文化象徵，並帶來動漫產業的藝術和技術的復興。這部電視動畫的人物、音樂和部分場景已

## <font color=#FF0000>範例2：從爬取的文章內容中，擷取出有外部連結的關鍵字。這些關鍵字在文章中是以藍色字體顯示，會連到外部的網頁，並解釋其內容</font>

In [14]:
for ext_link in result_new:
    a_tag = ext_link.find_all('a', href=re.compile("^(/wiki/)((?!:)\S)*$"))
    if len(a_tag) > 0:
        for link_string in a_tag:
            a_link = link_string["href"]       # 外部連結的網址
            a_keyword = link_string.get_text()  # 外部連結的中文名稱
            print("外部連結: [%s] %s" % (a_keyword, a_link))

外部連結: [華語] /wiki/%E5%8D%8E%E8%AF%AD
外部連結: [中國大陸] /wiki/%E4%B8%AD%E5%9B%BD%E5%A4%A7%E9%99%86
外部連結: [庵野秀明] /wiki/%E5%BA%B5%E9%87%8E%E7%A7%80%E6%98%8E
外部連結: [GAINAX] /wiki/GAINAX
外部連結: [龍之子製作公司] /wiki/%E9%BE%99%E4%B9%8B%E5%AD%90%E5%88%B6%E4%BD%9C%E5%85%AC%E5%8F%B8
外部連結: [日本動畫] /wiki/%E6%97%A5%E6%9C%AC%E5%8A%A8%E7%94%BB
外部連結: [電視連續劇] /wiki/%E7%94%B5%E8%A7%86%E8%BF%9E%E7%BB%AD%E5%89%A7
外部連結: [東京電視台] /wiki/%E4%B8%9C%E4%BA%AC%E7%94%B5%E8%A7%86%E5%8F%B0
外部連結: [日語] /wiki/%E6%97%A5%E8%AF%AD
外部連結: [配音] /wiki/%E9%85%8D%E9%9F%B3
外部連結: [碇真嗣] /wiki/%E7%A2%87%E7%9C%9F%E5%97%A3
外部連結: [歌手] /wiki/%E6%AD%8C%E6%89%8B
外部連結: [緒方惠美] /wiki/%E7%B7%92%E6%96%B9%E6%83%A0%E7%BE%8E
外部連結: [綾波零] /wiki/%E7%B6%BE%E6%B3%A2%E9%9B%B6
外部連結: [林原惠] /wiki/%E6%9E%97%E5%8E%9F%E6%83%A0
外部連結: [惣流·明日香·蘭格雷] /wiki/%E6%83%A3%E6%B5%81%C2%B7%E6%98%8E%E6%97%A5%E9%A6%99%C2%B7%E8%98%AD%E6%A0%BC%E9%9B%B7
外部連結: [宮村優子] /wiki/%E5%AE%AE%E6%9D%91%E5%84%AA%E5%AD%90
外部連結: [音樂] /wiki/%E6%96%B0%E4%B8%96%E7%B4%80%E7%A6%8F%E9%9F%B3%E6%88%B0%E5%A3%AB%E

### <font color=#FF0000>作業：接下來定義一個爬蟲函數，這個函數的主要工作為：</font>
#### (1) 爬取當前關鍵字的解釋，並存入檔案(因為文章內容太多會佔滿整個頁面，所以存程檔案，方便後續檢視)
#### (2) 萃取出當前關鍵字所引用的外部連結，當作新的查詢關鍵字
#### (3) 把第(2)擷取到的關鍵字當作新的關鍵字，回到第(1)步，爬取新的關鍵字解釋。

In [19]:
@retry
def crawler_function(lang_type, key_word, recursive ):
    if(recursive <= max_recursive):
        print("第[%d]層 - %s (%s)" % (recursive, lang_type, key_word))
        
        header ={'user-agent':ua.random}
        url = 'https://zh.wikipedia.org' + lang_type
        response = requests.get(url, headers=header)
        soup = BeautifulSoup(response.text, "lxml")
        print(url)
        
        title = soup.find('h1',attrs={'class':'firstHeading','id':'firstHeading'})
        f = open(title.text, 'w', encoding="utf-8")
        
        article = soup.find('div',attrs={'class':"mw-parser-output"}).find_all('p')
        
        # Part 1: 請參考範例1，爬取當前關鍵字的文章內容。
        #         因為內容太多，我們把它寫入檔案，並以關鍵字作為檔案名稱，以便稍後查閱內容。
        #         請先建立一個名為"WikiArticle"的資料夾，爬取到的文章內容會放在這個資料夾底下。
        for i in article:
            print(i.text)
            f.write(i.text)
            f.write('\n')
        f.close()
        
        # Part 2: 請參考範例2，萃取出本篇文章中所延伸引用的外部連結，並儲存在external_link_dict
        external_link_dict = dict({})

        for external_link in article:
            a_tag = external_link.find_all('a',href=re.compile('^(/wiki/)((?!:)\S)*$'))
            for i in a_tag:
                a_link = i["href"]
                a_name = i.text
                external_link_dict.setdefault(a_name,a_link)
                #print("外部連結: [%s] %s" % (a_name, a_link))
        #print(external_link_dict)
        #print(len(external_link_dict))
                
        # Part 3: 將Part 2所收集的外部連結，當作新的關鍵字，繼續迭代深入爬蟲
        if (len(external_link_dict) > 0):
            recursive = recursive + 1  # 遞迴深度加1
            for k, v in external_link_dict.items():
                crawler_function(v, k, recursive)  # 再次呼叫同樣的函數，執行同樣的流程
        
        
        
        
max_recursive = 1        
os.chdir("/tommy/WikiArticle");
crawler_function(lang_type, key_word, 0  )

第[0]層 - /zh-tw/%E6%96%B0%E4%B8%96%E7%BA%AA%E7%A6%8F%E9%9F%B3%E6%88%98%E5%A3%AB ( 新世紀福音戰士)
https://zh.wikipedia.org/zh-tw/%E6%96%B0%E4%B8%96%E7%BA%AA%E7%A6%8F%E9%9F%B3%E6%88%98%E5%A3%AB
《新世紀福音戰士》（日語：新世紀エヴァンゲリオン[注釋 1]；英語：Neon Genesis Evangelion[注釋 2]，通常被稱為EVANGELION[11]、NGE[12][13][14][15]或者EVA[5][16][17][18]。在華語圈中被翻譯為新世紀福音戰士[注釋 3][5][20]，中國大陸早期引進時譯為新世紀天鷹戰士[21][22]）是一部由庵野秀明執導，GAINAX和龍之子製作公司製作的日本動畫電視連續劇，於1995年10月至1996年3月在東京電視台首播。原版的日語配音演員，包括為碇真嗣配音的配音演員及歌手緒方惠美，為綾波零配音的林原惠和為惣流·明日香·蘭格雷配音的宮村優子等。劇中音樂由鷺巢詩郎製作，配樂專輯一經推出就登頂公信榜排行榜；動畫主題曲在其發布後的十幾年間有著持續的影響力。其他新世紀福音戰士系列作品還包括分別於1997年和1998年上映的三部電影，以及被稱作新劇場版的電影四部曲系列作，另外還有其他一些衍生動畫、漫畫和電子遊戲系列。

《新世紀福音戰士》[注釋 4]是一部有著機甲風格的後世界末日動畫。故事背景設置在未來、一場世界性的大災難發生十五年後的東京。故事圍繞著主人公——一名十幾歲的男孩碇真嗣，突然被神秘組織NERV招募去駕駛一種巨大的的生物兵器——EVA，與被稱為使徒的可怕不明敵人進行戰鬥而展開。故事最初著重表現戰鬥場景和人物之間的對話，隨著故事情節的發展，逐漸轉為對人物內心世界的剖析。

《EVA》整個系列突出呈現宗教象徵和主題（英語：Religious symbol），包括卡巴拉、基督教、猶太教以及神道教意象，被譽為20世紀90年代最成功和最負盛名的日本動畫之一。動畫業界和許多動漫欣賞者也將其視為日本最偉大的動畫之一。《EVA》同樣也是最受爭議的動畫電視連續劇之一。其同時混搭批判和機甲風格的解構，使得系列成為一種文化象徵，並帶來動漫產業的藝術和技術的復興

https://zh.wikipedia.org/wiki/%E5%8D%8E%E8%AF%AD
現代標準漢語[4]，亦稱新國音、標準漢語、華語，是其中一種漢語之標準語與通用語。它以北京官話为基础音、官話白話文著作为语法规范與書面文體。其廣泛通行於華人地區，但在各地有不同標準與稱呼，依通行地區分為三套標準：於中华人民共和国為“普通话”，中華民國為“國語”，在新加坡和马来西亚等東南亞国家為“華語”，香港和澳門則會並稱「國語」和「普通話」。

1923年中華民國教育部國語統一籌備會決定基於現代北方的官话白话文語法和北京話語音制定「新國音」，以取代老國音，1932年經中華民國教育部頒佈《國音常用字匯》後，被採納為中國的官方語言。當前在中国大陆、台灣均為實務上的官方語言，在新加坡則是官方語言之一，也是东南亚及其他海外華人群体除粵語外廣泛採用的其中一種中文通用語；且作為聯合國六種正式語文之一[註 1]，成為國際人士學習中文的主要參照。

中国大陸的「普通話」、臺灣的「國語」與東南亞地區的「華語」在語音與詞彙上存在一些差別。現代標準漢語在世界各地的口语中出現许多的腔調變體，如臺灣國語（受臺灣話腔調影響）和新馬華語（即马来西亚华语及新加坡华语，用词习惯受閩南語、粵語、馬來語及英语影響较多）等；而身為漢語起源地的中國內部更出现更多腔調變體，衍生出各种带有地方特色的「地方普通話」。

在兩岸三地和東南亞，官方和非官方組織對現代標準漢語的定義各有不同：

現代標準漢語是现代汉语口语与书面语的官定标准，基于现代北方汉语的语法和语音，做为官方、教学、媒体等的标准用语。

1955年，中华人民共和国全国文字改革会议把「國語」改称「普通话」[5]，意为“普遍共通、普遍通用”之全國共通語言，中华人民共和国国务院发出关于推广普通话的指示，就是「以北京语音为标准音，以北方话为基础方言，以典范的现代白话文著作为语法规范」，以“推广普通话”为重要的政策之一。[6][7]

港澳地區常將「國語」一詞作為現代標準中文的別稱。在香港、澳門，粵語是通行語言也是政府工作語言，政府不強制推廣普通話，不少中小學校以粵語為教學語言，但都教授普通話。澳門特別行政區政府以及民間機構均通過不同方式推行普通話[8]，但民間交流仍然使用粵語。在香港，粵語和英語已成為社會主流語言和定型語言，粵、英夾雜地講話極為普遍。在政府部門、法

https://zh.wikipedia.org/wiki/%E4%B8%AD%E5%9B%BD%E5%A4%A7%E9%99%86
中国大陆，是一个政治与法律术语。在中华人民共和国及其特别行政区法律中，中国大陆（或稱為大陸、祖國大陆[1]）是指除香港、澳门、臺灣以外的中华人民共和国主张管辖区。而在中华民国法律中，大陆地区（或稱為中国大陆[2]、大陆）是指除台湾地区以外的中华民国主张管辖区，部分情況下包括香港及澳門。

「中国大陆」作为法律术语，常用于与台湾同时出现的语境。除此之外，“中国大陆”一词也在政经关系、地理科学、学术讨论等场合有所运用。[註 1]

本法下列用语的含义：
出境，是指由中国内地前往其他国家或者地区，由中国内地前往香港特别行政区、澳门特别行政区，由中国大陆前往台湾地区。
入境，是指由其他国家或者地区进入中国内地，由香港特别行政区、澳门特别行政区进入中国内地，由台湾地区进入中国大陆。

1958年9月4日，全国人大常委会通过的《中华人民共和国政府关于领海的声明》中即指出，“中华人民共和国的领海宽度为12海里。这项规定适用于中华人民共和国的一切领土，包括中国大陆及其沿海岛屿，和同大陆及其沿海岛屿隔有公海的台湾及其周围各岛、澎湖列岛、东沙群岛、西沙群岛、中沙群岛、南沙群岛以及其他属于中国的岛屿[3]。”

1987年10月16日，中华人民共和国国务院办公厅发布《中华人民共和国国务院办公厅关于台湾同胞来祖国大陆探亲旅游接待办法的通知》，通知指出“台湾同胞回祖国大陆探亲旅游，须申请办理旅行证件。在香港地区，由中国外交部驻香港签证办事处办理，或由香港中国旅行社代办；在美国，日本或其他国家，由中国驻外使、领馆办理旅行证件[4]。”

2013年，全国人大常委会通过的《中华人民共和国出境入境管理法》第八十九条载明，“出境，是指由中国内地前往其他国家或者地区，由中国内地前往香港特别行政区、澳门特别行政区，由中国大陆前往台湾地区”[5]。该法将“中国大陆”与台湾地区对应，将“中国内地”与香港特别行政区、澳门特别行政区对称[5]，而在英文版中两词统一翻译为“Chinese mainland”[6][註 2]。

对大陆、台湾、香港或澳门的提述（不论是单独提述或同时提述），须解释为对作为中华人民共和国一个组成部分的大陆、台湾、香港或澳门（视属何情况而定）的提述。

1

https://zh.wikipedia.org/wiki/%E9%BE%99%E4%B9%8B%E5%AD%90%E5%88%B6%E4%BD%9C%E5%85%AC%E5%8F%B8
龍之子製作公司（株式会社タツノコプロダクション，2013年之前公司名原是以漢字方式寫作「株式会社竜の子プロダクション」，並常被簡稱為「タツノコプロ」或「竜の子プロ」），為一間日本動畫製作公司。1962年由當時備受讚賞的動畫界先驅者吉田龍夫跟其弟吉田健二及吉田豐治成立。這製片廠的名稱在日文中含有雙重意義——「タツ」（Tatsu）是吉田龍夫的暱稱，因此可解釋作「龍夫之子」，但同時在日文中「龍之子」實際上是海馬之意，這也是該公司的商標是一隻海馬的原因。

龍之子製作公司成立以後，專注於電視製作；這與競爭對手東映動畫主要參與特攝片有所不同，東映動畫那時也只是剛起步涉足電視製作而已。龍之子的處子之作為電視動畫《宇宙王牌》（宇宙エース，暫譯），及後也跟業界的傳奇人物真下耕一、押井守、庵野秀明（參與《新世紀福音戰士》的動畫製作）、笹川浩、山田勝久等合作。較出色的動畫被製成了翻譯後製版本，當中笹川浩的《馬赫GoGoGo》（マッハGoGoGo）、《科學小飛俠》及《功夫貓黨》都成功令世界注視日本動畫。

龍之子的動畫作品題材和取名都較科學化。但童話式的奇幻故事，如1970年代、1980年代的《昆蟲物語》（昆虫物語 みなしごハッチ）、樫の木モック、森の陽気な小人たち ベルフィーとリルビット以及《聖經》為本的《動畫親子劇場》（アニメ親子劇場）均同樣是龍之子出品。

1982年，龍之子提供《超時空要塞》電視動畫製作支援，換取海外的動畫和周邊商品發行權。1984年，龍之子授權Harmony Gold於北美發行此作。及後因Harmony Gold於北美、歐洲等地註冊《超時空要塞》商標，此舉大大損害了主要贊助商Big West的權益，Big West因而在2000年對龍之子提出了訴訟。2003年，法院裁定，龍之子有《超時空要塞》電視動畫（1982年版）的發行權，但不包括原有人物設計及機械設計的擁有權。

2005年，Takara購入了龍之子的大部份股份[1]。2006年，龍之子變成了Takara Tomy的附屬分支。

部份知名的日本動畫公司都跟龍之子有淵源。1979年成立的Studio Pierrot，是前龍之

https://zh.wikipedia.org/wiki/%E6%97%A5%E8%AF%AD
日語（ 日本語／にほんご Nihongo ?），又称为日本語，屬日本－琉球語系，是一種主要為日本列島上大和民族之间所使用的語言。日本并沒有在法律上明確規定日語為官方語言，但各种法令[註 1]都规定需使用日语，在学校教育中作为国语教授的也是日语。日語是日本的公用語言，是日本事實上的官方語言，類似於美國的英語的事實上的國語地位。

雖然并沒有精確的日語使用人口的統計，不過計算日本國內的人口以及居住在日本國外的日本人和日僑，日語使用者應超過一億三千萬人[2]。幾乎所有在日本出生長大的日本國民[註 2]都以日語為母語[註 3]。此外，對於失聰者，有對應日語文法及音韻系統的日本手語存在。

在日语语法学界，如果无特别说明，「日語」（日本語）这个詞彙，一般是指以江戶山手地區（今東京中心一帶）的中流階層方言為基礎的日语現代標準語[3][註 4]，有時也稱作「共通語」（共通語）。

日語在音韻方面，除了促音「っ」和撥音「ん」外，開音節（以元音结束的音节）語言的特徵強烈。此外包括標準發音在內的眾多方言都具有音拍（mora）。在重音方面，屬於音高重音（pitch accent，或謂非重音語言）。自古流傳至今的和語具有以下特徵：

（参看「#书写系统」一节和「音韻」一节）

在語序方面，句子主要由主語、賓語、謂語的順序構成，且是具代表性的話題優先語言之一。修飾語位於被修飾語之前。另外日語在表現名詞的格時，并不是通過改變語序或語尾，而是通過在詞后加具有語法功能的機能語（助詞）來表現。因此在語言類型學上，日語屬於主賓謂結構；在形態學上，日語屬於黏著語（参看语法一节）。

在词汇方面，除了自古傳下來的和语词外，還有中國傳入的汉语词。自近代之後，以西方語言為中心各國傳入的外來語的比例也逐漸增加。（参看词汇的种类一节）

在對人表現上，日語顯得極富變化；不單有口語和書面語的區別，還有普通和鄭重、男與女、老與少等的區別。日語擁有在語法和詞彙上均很發達的敬語體系，以表達叙述人物之間微妙的關係。（参看敬语一节）

日語也有多樣的方言系統，特別是在琉球群島，方言之間有著很大的差異（参看「方言」一节）。直到近世（江户时代）中期，京都作為日本的政治和文化中心，京都方言都有著標準語的地位[4]。在近世後期，德川幕府

...

https://zh.wikipedia.org/wiki/%E9%B2%81%E9%82%A6%E4%B8%89%E4%B8%96_(TV%E7%AC%AC1%E6%9C%9F)


《鲁邦三世》（日语：ルパン三世）是日本在1971年10月24日到1972年3月26日期間播出的電視動畫系列第一期共23集[1][2]，改編自加藤一彥（モンキー・パンチ）的漫畫作品《鲁邦三世》。



 铁臂阿童木 |  巨人之星 |  鬼太郎 |  人造人009

 机动战士高达 |  鲁邦三世 (TV第1期) |  銀河鐵道999 |  高立的未来世界

 福星小子 |  七龙珠 |  超时空要塞 |  足球小將

 美少女戰士 |  新世纪福音战士 |  数码宝贝大冒險 |  勇者王

 鋼之鍊金術師 |  涼宮春日的憂鬱 |  光之美少女 |  攻殼機動隊 STAND ALONE COMPLEX

 魔法少女小圓 |  進擊的巨人 |  少女与战车 |  歌之王子殿下

第[1]層 - /wiki/%E9%AB%98%E7%AB%8B%E7%9A%84%E6%9C%AA%E4%BE%86%E4%B8%96%E7%95%8C (未來少年柯南)
https://zh.wikipedia.org/wiki/%E9%AB%98%E7%AB%8B%E7%9A%84%E6%9C%AA%E4%BE%86%E4%B8%96%E7%95%8C
《未來少年柯南》（日语：未来少年コナン）是宮崎駿首度擔任導演的電視動畫作品，改編自美國作家亞歷山大·凱伊（Alexander Key（英语：Alexander Key））1970年發表的科幻小說《恐怖海嘯》（The Incredible Tide（英语：The Incredible Tide）），但內容已經過大幅潤色，與原作差異甚多。

於1978年4月4日至10月31日期間，每週二在日本廣播協會播出，全26集[1]。在香港由無綫電視翡翠台獲得播映權，於1980年首播，本動畫是無綫電視少數足本播映的動畫之一（即包括原裝片頭回顧及過場，廣播法例要求刪剪的內容除外）。在台灣最初曾由中華電視公司購得，並譯為《阿丹歷險記》在媒體上介紹，但最後卻並未播出，後來於1990年代由中視和衛視中文台播出。

西元2008年戰爭再次爆發，威力超越核武器的超磁力兵器投入戰場，半

https://zh.wikipedia.org/wiki/%E8%B6%B3%E7%90%83%E5%B0%8F%E5%B0%87
《足球小將》（日语：キャプテン翼，英語：Captain Tsubasa），或譯為《足球小将翼》、《足球小子》，中文直譯為《隊長小翼》，（臺灣的電玩版譯為《天使之翼》）是高橋陽一創作的日本漫畫，在日本及非日語圈均廣為人知。作品於1981年開始連載，講述了足球技術高超的少年大空翼從小學六年級開始到進入職業足壇後所發生的故事。包含續作在内，全系列漫畫的世界累計發行量已超過8000萬冊[1]。

由《足球小將》到現在的《足將小將 Golden-23》之中，世界正處於足球的黃金時代。無論日本國內，還是世界各地，都出現過不少優秀的足球選手。除此之外，亦有眾多的非球員角色一直支援故事的發展。有關故事中出現的人物簡介，請至「足球小將角色列表」條目。

漫畫故事主要分為四部長篇，分別是最初的《足球小將》、目標為爭奪世青盃的《足球小將世青篇》、以大空翼加盟西甲球隊—巴塞隆納作為主線的《足球小將 ROAD TO 2002》及爭取奧運冠軍的故事—《足球小將 Golden-23》。另外，亦有多部短篇故事及外傳，部分收錄於長篇或短篇集當中。

小學篇介紹了主角大空翼和其他主要角色，包括石崎了、若林源三、羅勃特本鄉、岬太郎、日向小次郎、三杉淳、松山光等人的背景和在全國大賽中的比賽。故事早段講述主角大空翼遷居至南葛市，因他就讀的南葛小學與修哲小學爭拗場地使用權，認識修哲小學的隊長兼守門員若林源三，並在單挑時打敗了他，若林源三不憤被打敗，最後在兩校友中不分高下。之後全國大賽展開，大空翼的出色的足球技術及得分能力使各人神服故邀請大空翼加盟南葛代表隊，與若林源三成為隊友出戰全國大賽。他的天賦才能震驚了整個足球界，而該年日本小學足球界亦人才輩出，當年司職前鋒的大空翼帶領的南葛在分組賽首場敗給了日向小次郎率領的明和小學（這場比賽也是全系列中，有大空翼出場而唯一輸過的比賽），但及後先後打敗立花兄弟的花輪隊、鋼門中西的難波隊、及三杉淳的武藏隊殺入決賽，再鬥明和小學。在若林源三復出下終於在加時打敗鬥志頑強的明和隊奪得冠軍。

中學篇仍然是描述在日本舉行的全國中學生足球比賽，不過加插了不少新人物，包括速度快及擅長隼射門的大友中學前鋒新田瞬、來自大阪東一中學的王牌後衛殺手早田誠、來自九

https://zh.wikipedia.org/wiki/%E6%95%B8%E7%A2%BC%E5%AF%B6%E8%B2%9D%E5%A4%A7%E5%86%92%E9%9A%AA
第[1]層 - /wiki/%E6%95%B8%E7%A2%BC%E5%AF%B6%E8%B2%9D%E5%A4%A7%E5%86%92%E9%9A%AA (數碼寶貝大冒險)
https://zh.wikipedia.org/wiki/%E6%95%B8%E7%A2%BC%E5%AF%B6%E8%B2%9D%E5%A4%A7%E5%86%92%E9%9A%AA


《数码宝贝大冒险》（日语：デジモンアドベンチャー，英语：Digimon Adventure），是1999年3月7日到2000年3月26日，每周日上午9:00在富士电视台系列播映的电视动画，是数码宝贝电视动画系列的第一作。[1]中国大陆搜狐视频2015年版权到期后，转由爱奇艺和银河奇异果网络独播。台灣由愛奇藝台灣站網路獨播。[2]

数码兽的主要「培養」要素並未全部出現，是暫時進化後再退化回原樣，吸收變身英雄的要素，數碼世界此假想空間和作為現實世界的東京·御台場流利地鏈接，成為連當時的世界觀也使之反映，加上作品出色質感成為之後作品的基礎；但孩子們被「選召」是被動參與此次冒險，消極被動的表現，阿丈等人也曾對此發表疑惑，而為了消除這種被動對當代少年的影響，在《数码宝贝驯兽师之王》中，“選召”這個概念被拋棄，轉變為主動前往數碼世界。该作在十多年后的2011年“生日”，pixiv上仍有多幅纪念作品获得排行前50位的记录，可见其影响力。其中剧场版《数码宝贝大冒险 最后的进化 绊》于2020年2月21日上映，讲述成为大学生的八神太一（22岁）他们与数码兽们最后的大冒险物语。

故事描写了以同名剧场版《数码宝贝大冒险》为舞台（1995年）4年后（1999年）的世界。

名为“数码世界”的假象世界与现实世界的东京（尤其是御台场、光丘两个地方）机缘巧合地连在了一起，主角一行孩子们被突然抛进了异世界中，他们在与数码宝贝和伙伴的一些列事件中一边发现自我一边成长，描写了孩子们共同活下去的成长故事。一点点被揭露的孩子们的过去，作为被选召理由的光丘之谜等，巧妙的伏笔随处可见，想方设法地“连大人们也待在其中”。[注 7]另外，还是一部反映父母离婚和死別

https://zh.wikipedia.org/wiki/%E9%8B%BC%E4%B9%8B%E9%8D%8A%E9%87%91%E8%A1%93%E5%B8%AB_(%E5%8B%95%E7%95%AB)


 ANIPLEX 群英社→木棉花國際[1] 羚邦國際（代理）、亞洲影帶（發行）

 ANIPLEX 普威爾國際 羚邦國際（代理）、亞洲影帶（發行）

  Madman Entertainment  Funimation Entertainment Revelation Films→MVM Dybex THE LICENSING MACHINE（代理）、Abaira（發行） Estudios Lain（授權發行）  Panini Video（代理） Dynit（授權發行） Mega-Anime Swen Entretenimentos （代理）、Focus Filmes（發行）

《鋼之鍊金術師》，為同名漫畫改編的動畫，由BONES製作，全51集。

連載鋼鍊漫畫雜誌《月刊少年GANGAN》在2003年7月號發布製作動畫版的消息，後來有關方面宣佈動畫《鋼之鍊金術師》於10月4日下午6時開始在日本MBS/TBS系播放。播畢後，《劇場版 鋼之鍊金術師 香巴拉的征服者》於2005年7月在日本上映，同原作漫畫在海內外都掀起一陣熱潮。電視動畫和劇場版動畫獲選為2004年第八回和2005年第九回日本文部省文化廳媒體藝術祭動畫部門推薦的作品。

愛德華·艾力克及弟弟艾爾凡斯十分思念亡故的母親，進行人體鍊成失敗而付出代價，愛德失去左腳、艾爾則失去全身；為救弟弟，愛德以右手為代價，拉回艾爾的靈魂固定在鎧甲上。他們為回復身體，開始踏上尋找賢者之石的旅程……

因愛德裝上鋼製義肢「機械鎧」，所以在取得國家鍊金術師資格時、大總統給予「鋼」的稱號，人稱「鋼之鍊金術師」。

DISC1

DISC2

《鋼之鍊金術師特別版OVA》（鋼の錬金術師 PREMIUM COLLECTION）

 铁臂阿童木 |  巨人之星 |  鬼太郎 |  人造人009

 机动战士高达 |  鲁邦三世 (TV第1期) |  銀河鐵道999 |  高立的未来世界

 福星小子 |  七龙珠 |  超时空要塞 |  足球小將

 美少女戰士 |  新世纪福音战士 |  数码宝贝大冒險 |  勇者王

 鋼之

https://zh.wikipedia.org/wiki/%E5%B0%91%E5%A5%B3%E4%B8%8E%E6%88%98%E8%BD%A6














電視動畫片頭曲Logo

 第二話: 2019年6月15日
(全六話)
《少女與戰車》（日语：ガールズ&パンツァー，GIRLS und PANZER），是由Actas製作、水島努執導的原創動畫作品；此部動畫的漫畫版已先行在Media Factory《月刊Comic Flapper（日语：コミックフラッパー）》2012年7月號至2014年4月號連載，由漫畫家才谷屋龍一負責作畫。

2012年5月17日，於官方網站公開了作品首波宣傳影片以及角色視覺圖等相關資訊[4]。



[5]

[第二話] 　描述幾年前大洗戰車道社團荒廢(原因不知)，社團成員要先找到戰車，優花里(軍武宅)跟在主角組後面找戰車，這一話找到了38(t)戰車、89式戰車、M3李戰車、三號突擊砲F型，加上四號坦克D型，這一話主角的姊姊在報導中露面，一行人到美穗租屋處參觀，隔天美穗冷泉麻子登場，她因為早上起不來而又遲到了，戰車道的教官蝶野亞美登場，之後就是第一次訓練的劇情。 

[第三話] 　因為美穗不想當車長，希望能和同伴開心的練習戰車道，因此由沙織當車長，但是沙織對戰車不大了解也不擅長指揮，主角一行人還是因為她們經驗比較充份和冷泉麻子天才駕駛的功力贏了其他組別。這一話有提到二戰戰車靶心瞄準的技巧，還有之前練習中提到的用腳踢駕駛員的方式進行左右轉的方式。這一話提到了要和英國車種的學校進行練習賽(第一話開頭的部份)。  

[第四話] 　這一話大洗隊決定用一台戰車引誘對方到定點的方式進行戰鬥，結果大洗隊的訓練不足默契也不好，對於戰車道的策略還處於新手而打不中對方，一年級隊士氣太低棄車逃跑，會長組的38t不能行動，其他三台戰車逃到市區進行戰鬥，89式車太爛偷襲失敗被擊破，3號突擊砲擊破一台戰車，但因為戰車插了旗子太明顯被鎖定而失敗，最後主角被包圍的時候會長組的人快速修好了戰車支援被英國隊打爆，安康組的冷泉麻子神走位加上美穗的指揮破三台戰車，因為打不破對方旗車的裝甲而輸給英國隊。大洗隊把戰車改回原先的塗裝，後半段是五十鈴華的回合。最後是抽籤大洗隊第一輪要和桑達斯比賽。

[第五話] 　前半段主角們在戰車餐廳用餐時西住姐和黑森峰的副隊長

In [2]:
pip install retry

Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install retrying

  Created wheel for retrying: filename=retrying-1.3.3-py3-none-any.whl size=11435 sha256=4c2b98b832e609f29338b108bbe03d2db8f492bffcb0de7210b1d3c7e0be01e4
  Stored in directory: c:\users\user\appdata\local\pip\cache\wheels\f9\8d\8d\f6af3f7f9eea3553bc2fe6d53e4b287dad18b06a861ac56ddf
Successfully built retrying
Note: you may need to restart the kernel to use updated packages.


In [9]:
import random
from retrying import retry

@retry
def do_something_unreliable():
    
    if (random.randint(0, 10) > 1):
        print ("just have a test")
        raise IOError("Broken sauce, everything is hosed!!!111one")
    else:
        return ("Awesome sauce!")

print (do_something_unreliable())

SyntaxError: invalid syntax (<ipython-input-9-a1196317ac38>, line 7)